In [1]:

# os.environ["CUDA_VISIBLE_DEVICES"] = "0"
# import torch
# print(torch.cuda.device_count())
import IPython.display as ipd
import os
# os.environ['CUDA_HOME'] = '/home/ubuntu/miniconda3/envs/respair/lib/python3.11/site-packages/torch/lib/include/cuda'
import torch
torch.manual_seed(0)
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True

import random
random.seed(0)

import numpy as np
np.random.seed(0)

# load packages

%cd /home/ubuntu/Kanade_Project/Project_Kanade_SpeechModel/pkanade_24
from cotlet_phon import phonemize

import time
import random
import yaml
from munch import Munch
import numpy as np
import torch
from torch import nn
import torch.nn.functional as F
import torchaudio
import librosa
from nltk.tokenize import word_tokenize

from models import *
from Modules.KotoDama_sampler import tokenizer_koto_prompt, tokenizer_koto_text, inference, Longform, merging_sentences, trim_long_silences
from utils import *

import nltk
nltk.download('punkt_tab')

from nltk.tokenize import sent_tokenize

from konoha import SentenceTokenizer


sent_tokenizer = SentenceTokenizer()

%matplotlib inline
to_mel = torchaudio.transforms.MelSpectrogram(
    n_mels=80, n_fft=2048, win_length=1200, hop_length=300)
mean, std = -4, 4


def preprocess(wave):
    wave_tensor = torch.from_numpy(wave).float()
    mel_tensor = to_mel(wave_tensor)
    mel_tensor = (torch.log(1e-5 + mel_tensor.unsqueeze(0)) - mean) / std
    return mel_tensor

def compute_style_through_clip_through_clip(path):
    wave, sr = librosa.load(path, sr=24000)
    audio, index = librosa.effects.trim(wave, top_db=30)
    if sr != 24000:
        audio = librosa.resample(audio, sr, 24000)
    mel_tensor = preprocess(audio).to(device)

    with torch.no_grad():
        ref_s = model.style_encoder(mel_tensor.unsqueeze(1))
        ref_p = model.predictor_encoder(mel_tensor.unsqueeze(1))

    return torch.cat([ref_s, ref_p], dim=1)


def Kotodama_Prompter(model, text, device):
    
    with torch.no_grad():
        style = model.KotoDama_Prompt(**tokenizer_koto_prompt(text, return_tensors="pt").to(device))['logits']
    return style

def Kotodama_Sampler(model, text, device):
    
    with torch.no_grad():
        style = model.KotoDama_Text(**tokenizer_koto_text(text, return_tensors="pt").to(device))['logits']
    return style


device = 'cuda' if torch.cuda.is_available() else 'cpu'

config = yaml.safe_load(open("Configs/config_kanade.yml"))

# load pretrained ASR model
ASR_config = config.get('ASR_config', False)
ASR_path = config.get('ASR_path', False)
text_aligner = load_ASR_models(ASR_path, ASR_config)


KotoDama_Prompter = load_KotoDama_Prompter(path="Utils/Kotodama/prompt_enc/checkpoint-73285")
KotoDama_TextSampler = load_KotoDama_TextSampler(path="Utils/Kotodama/text_enc/checkpoint-22680")

# load pretrained F0 model
F0_path = config.get('F0_path', False)
pitch_extractor = load_F0_models(F0_path)

# load BERT model
from Utils.PLBERT.util import load_plbert
BERT_path = config.get('PLBERT_dir', False)
plbert = load_plbert(BERT_path)

model_params = recursive_munch(config['model_params'])
model = build_model(model_params, text_aligner, pitch_extractor, plbert, KotoDama_Prompter, KotoDama_TextSampler)
_ = [model[key].eval() for key in model]
_ = [model[key].to(device) for key in model]

params_whole = torch.load("Models/Style_Kanade_v02/Top_ckpt_24khz.pth", map_location='cpu')
params = params_whole['net']


for key in model:
    if key in params:
        print('%s loaded' % key)
        try:
            model[key].load_state_dict(params[key])
        except:
            from collections import OrderedDict
            state_dict = params[key]
            new_state_dict = OrderedDict()
            for k, v in state_dict.items():
                name = k[7:] # remove `module.`
                new_state_dict[name] = v
            # load params
            model[key].load_state_dict(new_state_dict, strict=False)
#             except:
#                 _load(params[key], model[key])


_ = [model[key].eval() for key in model]


from Modules.diffusion.sampler import DiffusionSampler, ADPM2Sampler, KarrasSchedule
diffusion_sampler = DiffusionSampler(
    model.diffusion.diffusion,
    sampler=ADPM2Sampler(),
    sigma_schedule=KarrasSchedule(sigma_min=0.0001, sigma_max=3.0, rho=9.0), # empirical parameters
    clamp=False
)

/home/ubuntu/miniconda3/envs/respair/lib/python3.11/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


/home/ubuntu/Kanade_Project/Project_Kanade_SpeechModel/pkanade_24
177


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'BertJapaneseTokenizer'. 
The class this function is called from is 'DistilBertJapaneseTokenizer'.
[nltk_data] Downloading package punkt_tab to /home/ubuntu/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
/home/ubuntu/Kanade_Project/Project_Kanade_SpeechModel/pkanade_24/models.py:895: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed duri

bert loaded
bert_encoder loaded
predictor loaded
decoder loaded
text_encoder loaded
predictor_encoder loaded
style_encoder loaded
diffusion loaded
text_aligner loaded
pitch_extractor loaded
mpd loaded
msd loaded
wd loaded


# Explaining the Inference

alpha and beta will determine the impact of the diffusion sampler. 
rate_of_speech will define pace of speech.
 
diffusion sampler may not work on all devices for the reason explained in the repo, in that case please turn it off by setting both to 0.


アルファとベータは、ディフュージョンサンプラーの影響を決定します。
ディフュージョンサンプラーはすべての端末で動作しない可能性があり、その理由はリポジトリで説明されています。その場合は、両方を0にしてください。そうすれば、ディフュージョンサンプラーと影響が完全に０になります。
"リコンストラクションヘッド"は、ディフュージョンネットを使用して48kHzまでアップサンプリングすることで、失われた周波数を復元しようとします。レイテンシーを改善したい場合や、その機能にそれほど影響がないと感じる場合は、それをオフにできます。

In [3]:
"""different speaker by switching the name. we then define how much should be the impact of the diffusion sampler. 
if the diffusion sampler works for you, it's recommended to use both Kotodama. otherwise, set alpha and beta to 0."""

japanese = "Kimiji: 人生は、果てしない探求の旅のようなもの。私たちは、自分自身や周囲の世界について、常に新しい発見をしていく。それは、時として喜びをもたらすこともあれば、困難に直面することもある。しかしそれら全てが、自分を形作る貴重な経験である。"

raw_jpn = japanese[japanese.find(":") + 2:] # factoring out the name of the speaker, since we don't need that for phonemization.
text = phonemize(raw_jpn)

Kotodama = Kotodama_Sampler(model, text=japanese, device=device) # provide the Japanese text, not the Phonemized version.

reference_dicts = {}

reference_dicts['1789_14289w'] = japanese

start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():

    wav = inference(model, diffusion_sampler, text, Kotodama, alpha=0.1, beta=0.5, diffusion_steps=10, embedding_scale=1.5, rate_of_speech=1.) 
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    display(ipd.Audio(wav, rate=24000, normalize=False))

RTF = 0.016579


In [56]:
raw_jpn = """この俺に何度も同じことを説明させるな！! お前たちは俺の忠告を完全に無視して、とんでもない結果を招いてしまった。これが最後の警告だ。次は絶対に許さないぞ！"""
prompt =f"""A male voice that resonates with deep, thunderous intensity. His rapid-fire words slam like aggressive drumbeats, each syllable charged with intense rage. The expressive tone fluctuates between restrained fury and explosive outbursts. \n text: {raw_jpn}"""
prompt

'A male voice that resonates with deep, thunderous intensity. His rapid-fire words slam like aggressive drumbeats, each syllable charged with intense rage. The expressive tone fluctuates between restrained fury and explosive outbursts. \n text: この俺に何度も同じことを説明させるな！! お前たちは俺の忠告を完全に無視して、とんでもない結果を招いてしまった。これが最後の警告だ。次は絶対に許さないぞ！'

In [69]:
text = phonemize(raw_jpn)

Kotodama = Kotodama_Prompter(model, text=prompt, device=device) # provide the prompt text, not the Phonemized version.

reference_dicts = {}

reference_dicts['1789_14289w'] = prompt

start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():

    wav = inference(model, diffusion_sampler, text, Kotodama, alpha=.5, beta=.05, diffusion_steps=10, embedding_scale=1.5, rate_of_speech=1.)
    wave = trim_long_silences(wav)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    display(ipd.Audio(wave, rate=24000, normalize=True))

RTF = 0.023575


In [42]:
raw_jpn = """私に何度も同じことを説明させないでよ！!! お前たちは私の忠告を完全に無視して、とんでもない結果を招いてしまった! これが最後の警告だ。次は絶対に許さないわよ！"""
prompt =f"""A female voice that resonates with extreme intensity and a slightly high pitch. Her rapid-fire words cascade like aggressive drumbeats, each syllable charged with raw anger. The expressive tone fluctuates between controlled fury and explosive outbursts. \n text: {raw_jpn}"""
prompt

'A female voice that resonates with extreme intensity and a slightly high pitch. Her rapid-fire words cascade like aggressive drumbeats, each syllable charged with raw anger. The expressive tone fluctuates between controlled fury and explosive outbursts. \n text: 私に何度も同じことを説明させないでよ！!!\u3000お前たちは私の忠告を完全に無視して、とんでもない結果を招いてしまった! これが最後の警告だ。次は絶対に許さないわよ！'

In [39]:
text = phonemize(raw_jpn) 

Kotodama = Kotodama_Prompter(model, text=prompt, device=device) # provide the prompt text, not the Phonemized version.

reference_dicts = {}

reference_dicts['1789_14289w'] = prompt

start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():

    wav = inference(model, diffusion_sampler, text, Kotodama, alpha=.1, beta=.5, diffusion_steps=10, embedding_scale=1.5, rate_of_speech=1.)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    display(ipd.Audio(wav, rate=24000, normalize=True))

RTF = 0.022258


In [13]:
text = phonemize(raw_jpn)

Kotodama = Kotodama_Prompter(model, text=prompt, device=device) # provide the prompt text, not the Phonemized version.

reference_dicts = {}

reference_dicts['1789_14289w'] = prompt

start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():

    wav = inference(model, diffusion_sampler, text, Kotodama, alpha=.0, beta=.0, diffusion_steps=10, embedding_scale=1., rate_of_speech=1.)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    display(ipd.Audio(wav, rate=24000, normalize=True))

RTF = 0.014008


In [190]:
sref1 = style
sref2 = compute_style_through_clip("/home/ubuntu/Kanade_Project/Project_Kanade_SpeechModel/pkanade_24/Inference/reference_sample_wavs/syuukovoice_200918_3_01.wav")

"""weighted combination, define which style should be the dominant. 50-50 may result in an entirely new speaker.
ウ付きの組み合わせを使うことで、どのスタイルが優位になるべきかを定義できます。50対50の比率だと、新しいスピーカーが生み出される可能性があります。ェイト"""

cook = (sref1 * .5 + sref2 * .5) # for emotion transfer [20 / 80] or [10 / 90] might be good.

# Cooking New Styles

you can mix multiple styles and weight them to create new styles. 

複数のスタイルを組み合わせ、重み付けすることで新しいスタイルを作り出すことができます。

In [ ]:
sref1 = compute_style_through_clip_through_clip("a/sample/that/is/not/too/short.wav")
sref2 = compute_style_through_clip_through_clip("a/sample/that/is/not/too/short.wav")

"""weighted combination, define which style should be the dominant. 50-50 may result in an entirely new speaker.
ウェイト付きの組み合わせを使うことで、どのスタイルが優位になるべきかを定義できます。50対50の比率だと、新しいスピーカーが生み出される可能性があります。"""

cook = (sref1 * .1 + sref2 * .9) # for emotion transfer [20 / 80] or [10 / 90] might be good.

In [ ]:
text = phonemize(raw_jpn)

reference_dicts = {}

reference_dicts['1789_14289w'] = prompt

start = time.time()
noise = torch.randn(1,1,256).to(device)
for k, path in reference_dicts.items():

    wav = inference(model, diffusion_sampler, text, cook, alpha=.0, beta=.0, diffusion_steps=10, embedding_scale=1., rate_of_speech=1.)
    rtf = (time.time() - start) / (len(wav) / 24000)
    print(f"RTF = {rtf:5f}")
    display(ipd.Audio(wav, rate=24000, normalize=True))

# Longform

The duration of the Samples generated by using the regular inference function is limited. but we can tokenize each paragraph and
 do a weighted Style Transfer similar to what you saw before to ensure the output is consistent.

there's no theoretical limit to the length of a sample produced by the Long Form algorithm. make sure your texts are not too short after tokenization. 

**日本語**

通常のinference functionを使用して生成されたサンプルの長さに限界があります。しかし、各段落をトークン化し、以前見たようなスタイル転送を重み付けして行うことで、出力の一貫性を確保することができます。
ロングフォームアルゴリズムで生成されるサンプルの長さには理論的な制限はありません。トークン化後のテキストが短すぎないことを確認してください。

In [25]:
raw_jpn = japanese[japanese.find(":") + 2:]
speaker = japanese[:japanese.find(":") + 2]

sentences = sent_tokenizer.tokenize(raw_jpn)
sentences = merging_sentences(sentences)

silence = 24000 * 0.5 # 500 ms of silence between outputs for a more natural transition
# sentences = sent_tokenize(text)
print(sentences)
wavs = []
s_prev = None
for text in sentences:
    
    text_input = phonemize(text)

    Kotodama = Kotodama_Sampler(model, text=speaker + text, device=device) 

    wav, s_prev = Longform(model, diffusion_sampler,
                            text_input, 
                              s_prev, 
                              Kotodama, 
                              alpha = .3, 
                              beta =.9, 
                              t = .8, 
                              diffusion_steps=10, embedding_scale=1.5, rate_of_speech=1.)
    wavs.append(wav)
    wavs.append(np.zeros(int(silence)))
    
print('Synthesized: ')
display(ipd.Audio(np.concatenate(wavs), rate=24000, normalize=False))
# print('Reference: ')
# display(ipd.Audio(path, rate=24000, normalize=True))

['この世には、言葉にできない悲しみがある。 それは、胸の奥に沈んでいくような重さで、時間が経つにつれて、じわじわと広がっていく。', '私は、その悲しみを抱えながら、日々を過ごしている。 言葉を発するたびに、心の中で何度も繰り返し、慎重に選び抜いている。', 'それは、痛みを和らげるための儀式のようなものだ.']


Synthesized: 
